<a href="https://colab.research.google.com/github/etwumbarima/duval_shortest_path/blob/main/getting_started_tutorials/rapids-pip-colab-template.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<a target="_blank" href="https://colab.research.google.com/github/rapidsai-community/showcase/blob/main/getting_started_tutorials/rapids-pip-colab-template.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Install RAPIDS into Colab"/>
</a>

# RAPIDS cuDF is now already on your Colab instance!
RAPIDS cuDF is preinstalled on Google Colab and instantly accelerates Pandas with zero code changes. [You can quickly get started with our tutorial notebook](https://nvda.ws/rapids-cudf). This notebook template is for users who want to utilize the full suite of the RAPIDS libraries for their workflows on Colab.  

# Environment Sanity Check #

Click the _Runtime_ dropdown at the top of the page, then _Change Runtime Type_ and confirm the instance type is _GPU_.

You can check the output of `!nvidia-smi` to check which GPU you have.  Please uncomment the cell below if you'd like to do that.  Currently, RAPIDS runs on all available Colab GPU instances.

In [1]:
# !nvidia-smi

#Setup:
This set up script:

1. Checks to make sure that the GPU is RAPIDS compatible
1. Pip Installs the RAPIDS' libraries, which are:
  1. cuDF
  1. cuML
  1. cuGraph
  1. cuSpatial
  1. cuxFilter
  1. cuCIM
  1. xgboost

# Controlling Which RAPIDS Version is Installed
This line in the cell below, `!python rapidsai-csp-utils/colab/pip-install.py`, kicks off the RAPIDS installation script.  You can control the RAPIDS version installed by adding either `latest`, `nightlies` or the default/blank option.  Example:

`!python rapidsai-csp-utils/colab/pip-install.py <option>`

You can now tell the script to install:
1. **RAPIDS + Colab Default Version**, by leaving the install script option blank (or giving an invalid option), adds the rest of the RAPIDS libraries to the RAPIDS cuDF library preinstalled on Colab.  **This is the default and recommended version.**  Example: `!python rapidsai-csp-utils/colab/pip-install.py`
1. **Latest known working RAPIDS stable version**, by using the option `latest` upgrades all RAPIDS labraries to the latest working RAPIDS stable version.  Usually early access for future RAPIDS+Colab functionality - some functionality may not work, but can be same as the default version. Example: `!python rapidsai-csp-utils/colab/pip-install.py latest`
1. **the current nightlies version**, by using the option, `nightlies`, installs current RAPIDS nightlies version.  For RAPIDS Developer use - **not recommended/untested**.  Example: `!python rapidsai-csp-utils/colab/pip-install.py nightlies`


**This will complete in about 5-6 minutes**

In [2]:
# This get the RAPIDS-Colab install files and test check your GPU.  Run this and the next cell only.
# Please read the output of this cell.  If your Colab Instance is not RAPIDS compatible, it will warn you and give you remediation steps.
!git clone https://github.com/rapidsai/rapidsai-csp-utils.git
!python rapidsai-csp-utils/colab/pip-install.py


Cloning into 'rapidsai-csp-utils'...
remote: Enumerating objects: 586, done.
remote: Counting objects: 100% (152/152), done.
remote: Compressing objects: 100% (70/70), done.
remote: Total 586 (delta 122), reused 82 (delta 82), pack-reused 434 (from 3)
Receiving objects: 100% (586/586), 191.99 KiB | 8.73 MiB/s, done.
Resolving deltas: 100% (296/296), done.
Installing RAPIDS remaining 24.12.* libraries
Using Python 3.11.11 environment at: /usr
Resolved 154 packages in 9.67s
 Downloaded cuspatial-cu12
 Downloaded libcuspatial-cu12
 Downloaded datashader
 Downloaded cucim-cu12
 Downloaded scikit-image
 Downloaded cugraph-cu12
Prepared 11 packages in 16.44s
Uninstalled 1 package in 25ms
Installed 11 packages in 42ms
 + cucim-cu12==24.12.0
 + cugraph-cu12==24.12.0
 + cuproj-cu12==24.12.0
 + cuspatial-cu12==24.12.0
 + cuxfilter-cu12==24.12.0
 + datashader==0.17.0
 + jupyter-server-proxy==4.4.0
 + libcuspatial-cu12==24.12.0
 + pyct==0.5.0
 - scikit-image==0.25.2
 + scikit-image==0.24.0
 + simp

# RAPIDS is now installed on Colab.  
You can copy your code into the cells below or use the below to validate your RAPIDS installation and version.  
# Enjoy!

In [3]:
import cudf
cudf.__version__

'24.12.00'

In [4]:
import cuml
cuml.__version__

'24.12.00'

In [5]:
import cugraph
cugraph.__version__

'24.12.00'

In [6]:
import cuspatial
cuspatial.__version__

'24.12.00'

In [7]:
import cuxfilter
cuxfilter.__version__

'24.12.00'

# Next Steps #

For an overview of how you can access and work with your own datasets in Colab, check out [this guide](https://towardsdatascience.com/3-ways-to-load-csv-files-into-colab-7c14fcbdcb92).

For more RAPIDS examples, check out our RAPIDS notebooks repos:
1. https://github.com/rapidsai/notebooks
2. https://github.com/rapidsai/notebooks-contrib

## Program starts here

In [9]:
import networkx as nx
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
import os
import cudf
import cugraph
from shapely.geometry import Point, LineString
from shapely.ops import nearest_points


In [11]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [13]:
path = "/content/drive/MyDrive/colab"

In [31]:
# road_network = gpd.read_file(r"/bin/Shapefiles/DuvalEdges3_Project.shp")
# bridges = gpd.read_file(r"/bin/Shapefiles/DuvalBridges_project.shp")
# schools = gpd.read_file(r"/bin/Shapefiles/Duval Schools.shp")
# /content/drive/MyDrive/colab/DuvalNodeProject.shp


road_network = gpd.read_file(f"{path}/DuvalNodeProject.shp")
road_network_edges = gpd.read_file(f"{path}/DuvalEdges3_Project.shp")
bridges = gpd.read_file(f"{path}/DuvalBridges_project.shp")
schools = gpd.read_file(f"{path}/Duval Schools.shp")

In [32]:
gdf_nodes = road_network[['y', 'x', 'geometry']]
gdf_edges = road_network_edges[['u', 'v', 'length', 'geometry']]

In [36]:
def nearest_node(gdf_nodes, point):
    """Find the nearest road network node to a given point."""
    nearest_geom = nearest_points(gdf_nodes.geometry.union_all(), point)[0]
    return gdf_nodes[gdf_nodes.geometry == nearest_geom].index[0]

In [38]:
a = gdf_nodes.geometry.union_all()

In [39]:
a

In [ ]:
bridges["nearest_node"] = bridges.geometry.apply(lambda x: nearest_node(gdf_nodes, x))
schools["nearest_node"] = schools.geometry.apply(lambda x: nearest_node(gdf_nodes, x))

In [ ]:
edges_df = cudf.DataFrame({
    "src": gdf_edges["u"].values,
    "dst": gdf_edges["v"].values,
    "weight": gdf_edges["length"].values
})
